# Master TECR file creation

## Adding Du_et_al lines to the master_file

### Define the requisite functions

In [17]:
# define the printing function
def set_contrast(data_description, master_set, set_1, set_1_description, set_2, set_2_description, verbose_printing = False, total_values = True):
    # print the original sets
    if total_values:
        print('\n{} in the master file: '.format(data_description), len(master_set))
        print('{} in the {} file: '.format(data_description, set_1_description), len(set_1))
        print('{} in the {} file: '.format(data_description, set_2_description), len(set_2))
    
    # contrast the sets
    extra_set_1 = master_set - set_1
    missing_set_1 = set_1 - master_set
    extra_set_2 = master_set - set_2
    missing_set_2 = set_2 - master_set
    if verbose_printing:
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_1_description), len(extra_set_1), '\n', extra_set_1)
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_2_description), len(extra_set_2), '\n', extra_set_2)
        print('\nMissing {} in the master file, versus {}: '.format(data_description, set_1_description), len(missing_set_1), '\n', missing_set_1)
        print('\nMissing {} in the master file, versus {}: '.format(data_description, set_2_description), len(missing_set_2), '\n', missing_set_2)
    else:
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_1_description), len(extra_set_1))
        print('Extra {} in the master file, versus {}: '.format(data_description, set_2_description), len(extra_set_2))
        print('Missing {} in the master file, versus {}: '.format(data_description, set_1_description), len(missing_set_1))
        print('Missing {} in the master file, versus {}: '.format(data_description, set_2_description), len(missing_set_2))
        
    return missing_set_1, missing_set_2


# add the units of logarithm to the Magnesium concentration
def isnumber(string):
    from numpy import nan
    
    if string is not nan and string not in ['', ' ', nan]:
        try:
            float(string)
            return True
        except:
            try:
                string.isnumeric()
                return True
            except:
                return False

### Merge the TECR scrapings

In [32]:
from datetime import date
from numpy import nan
import pandas
import re

empty = [nan, 'nan', None, ' ', '', 'NaN']

# import Du_et_al
du_2012 = pandas.read_excel('mmc2.xlsx', sheet_name = 'Table S1. TECRDB Keqs')
du_2012 = du_2012.fillna(' ')
du_2012.rename(columns = {'Reaction.1': 'reaction_string'}, inplace = True)
du_enzymes = set(du_2012['Reaction'])
du_references = set(du_2012['Reference_id'])

# import the master_file
master_file = pandas.read_csv('2021-08-18_master_with_DOIs.csv')
master_file = master_file.fillna(' ')
original_master_file_length = len(master_file)
column_nans = ['' for row in range(original_master_file_length)]
master_file.insert(4, 'CID Reaction:', column_nans)
for column in master_file:
    if re.search('Unnamed', column):
        del master_file[column]
display(master_file.head(5))

master_references = set(master_file['Reference ID:'])
master_striped_references = set()
for reference in master_references:
    if reference not in [' ']:
        substituted_reference = re.sub('_.+', '', reference)
        master_striped_references.add(substituted_reference)
master_enzymes = set(master_file['Enzyme:'])

# contrast the enzymes
missing_master_enzymes, missing_du_enzymes = set_contrast('enzymes', master_enzymes, master_enzymes, 'Master file', du_enzymes, 'Du et al.', verbose_printing = False)
missing_master_references, missing_du_references = set_contrast('references', master_striped_references, master_striped_references, 'Master file', du_references, 'Du et al.', verbose_printing = False)

for du_index, du_row in du_2012.iterrows():
    du_enzyme = du_row['Reaction']
    du_reference = du_row['Reference_id']
                 
    # add undescribed enzymes and citations
    if du_reference in missing_du_references or du_enzyme in missing_du_enzymes:
        # define the column values 
        add_enzyme = du_enzyme
        add_reference = du_reference
        add_method = du_row['Method']
        add_ec = du_row['EC value']
        add_cid_reaction = du_row['Reaction formula in CID format']
        add_reaction = du_row['reaction_string']
        add_k = du_row['K\'']
        add_temperature = du_row['T(K)']
        add_ionic_strength = du_row['Ionic strength']
        add_ph = du_row['pH']
        add_buffer = du_row['Buffer/reagents/solute added']
        if du_row['pMg'] not in [None, nan, ' ']:
            pmg = '{} = -log[Mg+2]'.format(du_row['pMg'])
        else:
            pmg = None
        add_conditions = ' _ '.join([du_row['media conditions'], du_row['electrolytes'], ''])
        add_conditions = re.sub('_\s+_', '', add_conditions)
        
        
        # add a new row at the end of master dataframe, according to master column organization
        master_file.loc[len(master_file.index)] = ['', add_enzyme, '', add_cid_reaction, add_reaction, '', du_reference, '', '', add_temperature, add_ph, add_k, '', add_method, add_buffer, add_conditions, add_ec, '', '', '', add_ionic_strength, '']   # ['standard_id', 'Enzyme:', 'KEGG Reaction:', 'CID_reaction', 'Reaction:', 'Reference:', 'Reference ID:', 'PMID', 'DOI', 'T [K]', 'pH ', 'Keq', 'Km', 'Method:', 'Buffer:', 'Experimental conditions', 'EC Value:', 'solutes [mol / kg]', 'solutes [mol / dm^3]', 'Ionic strength [mol / dm^3]', 'Ionic strength [mol / kg]', 'Enthalpy [kJ / mol]']
        
# strip spaces from the Pandas elements
for column in master_file:
    print(master_file[column])
    
    for index, entry in master_file[column].iteritems():
        if entry is float:
            master_file.at[index, column] = str(entry).strip(' ?~')
            master_file.at[index, column] = float(entry)
        elif entry is int:
            master_file.at[index, column] = str(entry).strip(' ?~')
            master_file.at[index, column] = int(entry)
        else:
            master_file.at[index, column] = str(entry).strip(' ?~')

                
csv_name = '2021-09-02_master_TECR_1.csv'
master_file.to_csv(csv_name)

C:\Program Files (x86)\Anaconda3\lib\site-packages\openpyxl\worksheet\_reader.py:296: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


standard_id                  Enzyme:  \
0      4336.0  aspartate ammonia-lyase   
1      2910.0  aspartate ammonia-lyase   
2      2129.0       fumarate hydratase   
3      2130.0       fumarate hydratase   
4       791.0       fumarate hydratase   

                            KEGG Reaction: CID Reaction:  \
0  kegg:C00049 = kegg:C00122 + kegg:C00014                 
1  kegg:C00049 = kegg:C00122 + kegg:C00014                 
2  kegg:C00122 + kegg:C00001 = kegg:C00149                 
3  kegg:C00122 + kegg:C00001 = kegg:C00149                 
4  kegg:C00122 + kegg:C00001 = kegg:C00149                 

                                      Reaction:  \
0  L-aspartate(aq) = fumarate(aq) + ammonia(aq)   
1  L-aspartate(aq) = fumarate(aq) + ammonia(aq)   
2        fumarate(aq) + H2O(l) = (S)-malate(aq)   
3        fumarate(aq) + H2O(l) = (S)-malate(aq)   
4        fumarate(aq) + H2O(l) = (S)-malate(aq)   

                                          Reference:   Reference ID:  \
0  Quastel J.H.; Woolf B.; Biochem. J.; 20 545 (1...  26QUA/WOO_1205   
1              Woolf B.; Biochem. J.; 23 472 (1929).      29WOO_1206   
2  Borsook H.; Schott H.F.; J. Biol. Chem.; 92 55...  31BOR/SCH_1141   
3  Borsook H.; Schott H.F.; J. Biol. Chem.; 92 55...  31BOR/SCH_1141   
4       Jacobsohn K.P.; Biochem. Z.; 274 167 (1934).      34JAC_1142   

       PMID                DOI   T [K]  ... Km  \
0  16743691  10.1042/bj0200545  310.15  ...      
1  16744231  10.1042/bj0230472  310.15  ...      
2                               298.15  ...      
3                               298.15  ...      
4                               278.15  ...      

                             Method:    Buffer: Experimental conditions  \
0                  chemical analysis  phosphate                           
1  chemical analysis and polarimetry  phosphate                           
2                   electrochemistry                                      
3                   electrochemistry                                      
4                        polarimetry   barbital                           

  EC Value: solutes [mol / kg] solutes [mol / dm^3]  \
0   4.3.1.1                                           
1   4.3.1.1                                           
2   4.2.1.2                                           
3   4.2.1.2                                           
4   4.2.1.2                                           

  Ionic strength [mol / dm^3] Ionic strength [mol / kg] Enthalpy [kJ / mol]  
0                                                                            
1                                                                            
2                                                                            
3                                                                            
4                                                                            

[5 rows x 22 columns]


enzymes in the master file:  492
enzymes in the Master file file:  492
enzymes in the Du et al. file:  413

Extra enzymes in the master file, versus Master file:  0
Extra enzymes in the master file, versus Du et al.:  92
Missing enzymes in the master file, versus Master file:  0
Missing enzymes in the master file, versus Du et al.:  13

references in the master file:  1015
references in the Master file file:  1015
references in the Du et al. file:  876

Extra references in the master file, versus Master file:  0
Extra references in the master file, versus Du et al.:  151
Missing references in the master file, versus Master file:  0
Missing references in the master file, versus Du et al.:  12
0       4336.0
1       2910.0
2       2129.0
3       2130.0
4        791.0
         ...  
5238          
5239          
5240          
5241          
5242          
Name: standard_id, Length: 5243, dtype: object
0                  aspartate ammonia-lyase
1                  aspartate ammonia-lyase


## Aligning Elad_file datum with master_file datum

### Define the requisite functions

In [17]:
# merging values between matched datum
def redefine_master(master_row, du_row, master_index, du_index):
    from numpy import unique
    empty = [nan, 'nan', None, ' ', '', 'NaN']
    
    # print the datum pair for manual inspection
    announcement = '\nmatched pair:'
    print(announcement, '\n', '='*len(announcement))
    print('du_index', du_index)
    print('master_index', master_index, '\n')
    
    # match CID reactions
    du_cid = du_row['Reaction formula in CID format']
    if master_row['CID Reaction:'] in empty:
        master_file.at[master_index, 'CID Reaction:'] = du_cid

    # match magnesium concentrations
    master_pmg = master_row['Experimental conditions']
    if du_row['pMg'] not in [None, nan, ' ']:
        pmg = '{} = -log[Mg+2]'.format(du_row['pMg'])
    else:
        pmg = None
    add_conditions = ' _ '.join([du_row['media conditions'], du_row['electrolytes'], ''])
    add_conditions = re.sub('_\s+_', '', add_conditions)
    if master_pmg in empty:
        master_file.at[master_index, 'Experimental conditions'] = add_conditions
        print(master_index, '\t', 'new pmg', '\t', master_file.at[master_index, 'Experimental conditions'])
    else:
        master_file.at[master_index, 'Experimental conditions'] = ' _ '.join([str(master_pmg), str(add_conditions)]) 
        print(master_index, '\t', 'new pmg', '\t', master_file.at[master_index, 'Experimental conditions'])            

    # match methods
    master_method = master_row['Method:']
    du_method = du_row['Method']
    if master_method == du_method:
        pass            
    elif master_method in empty:
        master_file.at[master_index, 'Method:'] = du_method
    elif du_method not in empty:
        master_methods = master_method.split(' and ')
        combined_methods = set([du_method] + master_methods)
        if combined_methods not in empty:
            combined_methods_string = ' and '.join([method for method in combined_methods])
        else:
            combined_methods_string = ' and '.join([du_method, master_method])
        
        master_file.at[master_index, 'Method:'] = combined_methods_string
        print(master_index, '\t', 'new method', '\t', master_file.at[master_index, 'Method:'])

    # match EC values
    master_ec = master_row['EC Value:']
    du_ec = du_row['EC value']
    if master_ec not in empty:
        master_ec = [master_ec]
        if master_ec[0] == du_ec:
            master_file.at[master_index, 'EC Value:'] = master_ec[0]   
        elif du_ec not in empty:
            if re.search('&', du_ec):
                du_ecs = du_ec.split('&')
                #du_ecs = [str(ec) for ec in du_ecs]
                total_ecs = unique(du_ecs + master_ec)
            else:
                total_ecs = [master_ec[0], du_ec]
            master_file.at[master_index, 'EC Value:'] = " & ".join(total_ecs)
            print(master_index, '\t', 'new EC', '\t', master_file.at[master_index, 'EC Value:'])
    else:
        master_file.at[master_index, 'EC Value:'] = du_ec

    # match ionic strength concentrations
    master_ionic_strength = master_row['Ionic strength [mol / dm^3]']
    du_ionic_strength = du_row['Ionic strength']
    if str(master_ionic_strength) == str(du_ionic_strength):
        pass            
    elif master_ionic_strength in empty:
        master_file.at[master_index, 'Ionic strength [mol / dm^3]'] = du_ionic_strength
    elif du_ionic_strength not in empty:
        master_file.at[master_index, 'Ionic strength [mol / dm^3]'] = " & ".join([str(master_ionic_strength), str(du_ionic_strength)])
        print(master_index, '\t', 'new ionic strength', '\t', master_file.at[master_index, 'Ionic strength [mol / dm^3]'])
        
    # match the standard_id 
    master_du_ud = 
    if master_id in empty:
        master_file.at[master_index, 'standard_id'] = elad_id
    elif elad_id is not nan and elad_id not in empty:
        master_file.at[master_index, 'standard_id'] = " & ".join([str(master_id), str(elad_id)])
        print(master_index, '\t', 'new standard_id', '\t', master_file.at[master_index, 'standard_id'])
    
# homogenize the charge format    
def charge_format(master_reaction):                                
    print(master_reaction)
    remove_string = re.search('\w(\d\-)', master_reaction).group(1)
    print(remove_string)
    master_reaction = re.sub(remove_string, '-{}'.format(remove_string), master_reaction)
    print(master_reaction)
    return master_reaction, remove_string

### Aligning datum values

In [71]:
# -*- coding: utf-8 -*-
from to_precision import sci_notation
from numpy import nan, unique
from datetime import date
import pandas
import json
import re

empty = [nan, 'nan', None, ' ', '', 'NaN']

# import the spreadsheets
du_2012 = pandas.read_excel('mmc2.xlsx', sheet_name = 'Table S1. TECRDB Keqs')
du_2012 = du_2012.fillna(' ')
du_2012.rename(columns = {'Reaction.1': 'reaction_string'}, inplace = True)

# standard_ids = [id for id in range(len(equilibrator_2008))]
# equilibrator_2008.insert(0, 'standard_id', standard_ids)
# equilibrator_2008.to_csv('TECRDB_Elad_Noor.csv')

master_file = pandas.read_csv('2021-09-02_master_TECR_1.csv')
master_file = master_file.fillna(' ')
for column in master_file:
    if re.search('Unnamed', column):
        del master_file[column]
        
# # establish standard IDs for each TECR datum
# original_master_file_length = len(master_file)
# column_nans = ['' for row in range(original_master_file_length)]
# master_file.insert(0, 'standard_id', column_nans)

# ========================================================================================================================================================        

matched_master_indices = []
display_count = 0
unmatched_entries = 0
errors_dictionary = {}
for du_index, du_row in du_2012.iterrows():
    matched_datum = False
    print('\ndu_index', du_index)
    
    # define Du et al. values for this datum
    du_enzyme = du_row['Reaction']
    du_reference = du_row['Reference_id']
    du_method = du_row['Method']
    du_ec = du_row['EC value']
    du_cid_reaction = du_row['Reaction formula in CID format']
    du_reaction = du_row['reaction_string']
    du_pmg = du_row['pMg']
    du_k = du_row['K\'']
    du_temperature = du_row['T(K)']
    du_ionic_strength = du_row['Ionic strength']
    du_ph = du_row['pH']
    add_conditions = ' _ '.join([du_row['media conditions'], du_row['electrolytes'], ''])
    add_conditions = re.sub('_\s+_', '', add_conditions)
    
    # determine the set of possible matches
    matching_master_subset = master_file.loc[(master_file['Enzyme:'] == du_enzyme)]    #  & (master_file['Keq'] == du_k) & (master_file['T [K]'] == du_temperature) & (master_file['pH '] == du_ph)
    if display_count < 5:
        display(matching_master_subset)
    display_count += 1
    
    errors = []
    for master_index, master_row in matching_master_subset.iterrows():  
        # remove previously matched rows
        if master_index in matched_master_indices:
            error = r''.join([str(x) for x in [master_index, '___','previously matched datum', '___', du_index]])
            errors.append(error)
            continue

        # define the master values for this datum 
        master_reference = master_row['Reference:']
        master_method = master_row['Method:']
        master_ec = master_row['EC Value:']
        master_pmg = master_row['Experimental conditions']
        master_ionic_strength = master_row['Ionic strength [mol / dm^3]']
        master_temperature = master_row['T [K]']
        master_ph = master_row['pH ']
        master_k = master_row['Keq']
        master_km = master_row['Km']
        master_reference_id = re.sub('_.+', '', master_row['Reference ID:'])
        master_reaction = master_row['Reaction:']
#         master_reaction = re.sub('\u00ce\u00b1|\u00ce\u00b2', '', master_reaction)
#         master_reaction = re.sub('\u00cf\u2030', '-w', master_reaction)

        # match the reference
        if du_reference != master_reference_id:
#             error = r''.join([str(x) for x in [master_index, '___', 'reference', '___', du_reference, '___', master_reference_id]])
#             errors.append(error)
            print(error)
            continue

        # match the temperature
        if (du_temperature and master_temperature) not in empty:
            du_temperature = re.sub('l', '1', str(du_temperature))
            master_temperature = re.sub('l', '1', str(master_temperature))
            if sci_notation(du_temperature, 2) != sci_notation(master_temperature, 2):
                error = r''.join([str(x) for x in [master_index, '___','temperature', '___', du_temperature, '___', master_temperature]])
                print(error)
                errors.append(error)
                continue

        # match the pH
        if (du_ph and master_ph) not in empty:
            du_ph = str(du_ph).strip('?~')
            master_ph = str(master_ph).strip('?~')
            if sci_notation(du_ph, 2) != sci_notation(master_ph, 2):
                error = r''.join([str(x) for x in [master_index, '___','ph', '___', du_ph, '___', master_ph]])
                print(error)
                errors.append(error)
                continue

        # match the Keq
        if re.search('\w(\?\w+)', str(master_k)):
            master_k = re.sub('(\?\w+)', '', str(master_k))

        if (du_k and master_k) is not nan and (du_k and master_k) not in empty:
            du_k = float(str(du_k).strip('~?'))
            master_k = float(str(master_k).strip('~?'))
            if sci_notation(du_k, 2) != sci_notation(master_k, 2):
                error = r''.join([str(x) for x in [master_index, '___', 'Keq', '___', du_k, '___', master_k]])
                print(error)
                errors.append(error)
                continue
                
        # match the reactions 
        if du_reaction != master_reaction:
            error = r''.join([str(x) for x in [master_index, '___', 'reaction', '___', du_reaction, '___', master_reaction]])
            print(error)
            errors.append(error)
#             if re.search('= -\w', master_reaction):
#                 remove_string = re.search('=(\s-)\w', master_reaction).group(1)
#                 master_reaction = re.sub(remove_string, '-', master_reaction)
#             if du_reaction != master_reaction:

#                 if re.search(' -D-', master_reaction):
#                     remove_string = re.search('\s(-D-)', master_reaction).group(1)
#                     master_reaction = re.sub(remove_string, 'D-', master_reaction, 1)
#                 if du_reaction != master_reaction:

#                     if re.search('\w\d\-', master_reaction):
#                         loop = True
#                         try:
#                             while loop:
#                                 master_reaction, remove_string = charge_format(master_reaction)
#                                 if remove_string is None:
#                                     loop = False
#                         except:
#                             pass
                        
#                     if du_reaction != master_reaction:

#                         if re.search('\(\w\)\-', master_reaction):
#                             master_reaction = re.sub('\(\w\)\-', '', master_reaction)
#                         if du_reaction != master_reaction:

#                             if re.search('-lipoate', master_reaction):
#                                 master_reaction = re.sub('(-lipoate)', 'lipoate', master_reaction, 1)
#                             if du_reaction != master_reaction:

#                                 error = ''.join([str(x) for x in [master_index, '___', 'reaction', '___', du_reaction, '___', master_reaction]])
#                                 print(error)
#                                 errors.append(error)
#                                 continue

        # define the new data of the master file
        matched_datum = True
        redefine_master(master_row, du_row, master_index, du_index)
        break

    if not matched_datum:
        print('--> Failed index to match: ', du_index, '___', du_enzyme)
        unmatched_entries += 1
        errors_dictionary[du_index] = errors
    else:
        matched_master_indices.append(master_index)
        
# test for standard_id uniqueness and unmatched values
print('\nCompletely unique standard_ids: ', len(matched_master_indices) == len(set(matched_master_indices)))
print('Unmatched standard_ids: ', unmatched_entries)
        
# export the unmatched datums
with open('2021-09-02_unmatched_Du_datums.json', 'w') as output:
    json.dump(errors_dictionary, output, indent = 3)

        
# export the combined master file
csv_name = '2021-09-02_master_TECR_2.csv'
master_file.to_csv(csv_name)


du_index 0


C:\Program Files (x86)\Anaconda3\lib\site-packages\openpyxl\worksheet\_reader.py:296: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


standard_id                Enzyme:  \
4265      1257.0  anthranilate synthase   
4266      1258.0  anthranilate synthase   
4267      1259.0  anthranilate synthase   
4268      1260.0  anthranilate synthase   
4269      1261.0  anthranilate synthase   

                                         KEGG Reaction: CID Reaction:  \
4265  kegg:C00251 + kegg:C00014 = kegg:C00108 + kegg...                 
4266  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...                 
4267  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...                 
4268  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...                 
4269  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...                 

                                              Reaction: Reference:  \
4265  chorismate(aq) + ammonia(aq) = anthranilate(aq...              
4266  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4267  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4268  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4269  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              

     Reference ID: PMID DOI   T [K]  ... Km  \
4265     00BYR/GOL           298.15  ...      
4266     00BYR/GOL           298.15  ...      
4267     00BYR/GOL           288.15  ...      
4268     00BYR/GOL           302.75  ...      
4269     00BYR/GOL           293.15  ...      

                                                Method: Buffer:  \
4265  calorimetry, spectrophotometry, and chromatogr...           
4266  calorimetry, spectrophotometry, and chromatogr...           
4267  calorimetry, spectrophotometry, and chromatogr...           
4268  calorimetry, spectrophotometry, and chromatogr...           
4269  calorimetry, spectrophotometry, and chromatogr...           

     Experimental conditions EC Value: solutes [mol / kg]  \
4265                          4.1.3.27                      
4266                          4.1.3.27                      
4267                          4.1.3.27                      
4268                          4.1.3.27                      
4269                          4.1.3.27                      

     solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
4265                                             0.56   
4266                                             0.14   
4267                                             0.15   
4268                                             0.14   
4269                                             0.15   

     Ionic strength [mol / kg] Enthalpy [kJ / mol]  
4265                      0.56                      
4266                      0.14                      
4267                      0.15                      
4268                      0.14                      
4269                      0.15                      

[5 rows x 22 columns]

4265___temperature___288.15___298.15
4266___temperature___288.15___298.15

matched pair: 
du_index 0
master_index 4267 

4267 	 new pmg 	 mol/kg;IS=0.15;Tricine=0.0465;(Na)1(OH)1=0.030967;(Mg)1(Cl)2=0.011233;chorismate=0.00005667;ammonia=0.09178;(Cl)1=0.09178;2-amino-2-deoxyisochorismate=0.0000494;(K)2(HPO4)1=0.003;(K)1(H2PO4)1=0.002;EDTA=0.000005;DTT=0.00001  

du_index 1


standard_id                Enzyme:  \
4265      1257.0  anthranilate synthase   
4266      1258.0  anthranilate synthase   
4267      1259.0  anthranilate synthase   
4268      1260.0  anthranilate synthase   
4269      1261.0  anthranilate synthase   

                                         KEGG Reaction:  \
4265  kegg:C00251 + kegg:C00014 = kegg:C00108 + kegg...   
4266  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...   
4267  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...   
4268  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...   
4269  kegg:C00251 + kegg:C00014 = kegg:C18054 + kegg...   

                                      CID Reaction:  \
4265                                                  
4266                                                  
4267  CHB_16134 + CHB_29748 = CHB_15377 + CHB_49197   
4268                                                  
4269                                                  

                                              Reaction: Reference:  \
4265  chorismate(aq) + ammonia(aq) = anthranilate(aq...              
4266  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4267  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4268  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              
4269  chorismate(aq) + ammonia(aq) = 2-amino-2-deoxy...              

     Reference ID: PMID DOI   T [K]  ... Km  \
4265     00BYR/GOL           298.15  ...      
4266     00BYR/GOL           298.15  ...      
4267     00BYR/GOL           288.15  ...      
4268     00BYR/GOL           302.75  ...      
4269     00BYR/GOL           293.15  ...      

                                                Method: Buffer:  \
4265  calorimetry, spectrophotometry, and chromatogr...           
4266  calorimetry, spectrophotometry, and chromatogr...           
4267  calorimetry, spectrophotometry, and chromatogr...           
4268  calorimetry, spectrophotometry, and chromatogr...           
4269  calorimetry, spectrophotometry, and chromatogr...           

                                Experimental conditions EC Value:  \
4265                                                     4.1.3.27   
4266                                                     4.1.3.27   
4267  mol/kg;IS=0.15;Tricine=0.0465;(Na)1(OH)1=0.030...  4.1.3.27   
4268                                                     4.1.3.27   
4269                                                     4.1.3.27   

     solutes [mol / kg] solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
4265                                                                0.56   
4266                                                                0.14   
4267                                                                0.15   
4268                                                                0.14   
4269                                                                0.15   

     Ionic strength [mol / kg] Enthalpy [kJ / mol]  
4265                      0.56                      
4266                      0.14                      
4267                      0.15                      
4268                      0.14                      
4269                      0.15                      

[5 rows x 22 columns]

...

2499___previously matched datum___4171
2499___previously matched datum___4171
2499___previously matched datum___4171
2499___previously matched datum___4171
3115___previously matched datum___4171
3115___previously matched datum___4171
3115___previously matched datum___4171
3115___previously matched datum___4171
3258___previously matched datum___4171
3258___previously matched datum___4171
3258___previously matched datum___4171
3258___previously matched datum___4171
3258___previously matched datum___4171

matched pair: 
du_index 4171
master_index 3966 

3966 	 new pmg 	 mol/L;Tris=0.05;(Mg)1(SO4)1=0.004;(Na)2(SO3)1=0.008  

du_index 4172
516___previously matched datum___4172
2499___previously matched datum___4172
2499___previously matched datum___4172
2499___previously matched datum___4172
2499___previously matched datum___4172
3115___previously matched datum___4172
3115___previously matched datum___4172
3115___previously matched datum___4172
3115___previously matched datum___4172
3258___

3968___previously matched datum___4193
4826___previously matched datum___4193
4890___temperature___338.15___348.15
4891___temperature___338.15___353.15
4892___temperature___338.15___333.15

matched pair: 
du_index 4193
master_index 4893 

4893 	 new pmg 	 mol/L;(Mg)1(SO4)1=0.004;(Na)2(SO3)1=0.008;Tris=0.05  

du_index 4194
516___previously matched datum___4194
2499___previously matched datum___4194
2499___previously matched datum___4194
2499___previously matched datum___4194
2499___previously matched datum___4194
3115___previously matched datum___4194
3115___previously matched datum___4194
3115___previously matched datum___4194
3115___previously matched datum___4194
3258___previously matched datum___4194
3258___previously matched datum___4194
3258___previously matched datum___4194
3258___previously matched datum___4194
3258___previously matched datum___4194
3968___previously matched datum___4194
4826___previously matched datum___4194
4890___temperature___343.15___348.15
4891___temperat

3999___Keq___16.51071124___17.7
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
5047___previously matched datum___4206
--> Failed index to match:  4206 ___ penicillin amidase

du_index 4207

matched pair: 
du_index 4207
master_index 4000 

4000 	 new pmg 	 mol/L; glycine-NaOH buffer=0.067;choline=0.005;ATP=0.0005;(Mg)1(SO4)1=0.01;DTT=0.0013  

du_index 4208
2501___previously matched datum___4208
2501___previously matched datum___4208
2501___previously matched datum___4208
2501___previously matched datum___4208
2501___previously matched datum___4208
2501___previously matched datum___4208
2501___previously matched datum___4208

matched pair: 
du_index 4208
master_index 4006 

4006 	 new pmg 	 mol/kg;IS=0.37;indole=0.00095;1-(ind

1443___previously matched datum___4251
3315___previously matched datum___4251
3315___previously matched datum___4251

matched pair: 
du_index 4251
master_index 4795 

4795 	 new pmg 	 3.0 = -log[Mg+2] _ mol/L;IS=0.25;Mg2+_free=0.001;K+_tot=0.2331;(Cl)1=0.1712;(HPO4)1=0.0139;(H2PO4)1=0.0361 _ Mg2+ (0.001 mol/L) _ 

du_index 4252
1443___previously matched datum___4252
3315___previously matched datum___4252
3315___previously matched datum___4252
4796___ph___6.7___8.2
4798___ph___6.7___7.0
4799___ph___6.7___7.13
4800___ph___6.7___7.0
4801___ph___6.7___7.4
4803___ph___6.7___7.0
4804___ph___6.7___7.0
4805___ph___6.7___7.8
4807___ph___6.7___7.0
4809___ph___6.7___7.0

matched pair: 
du_index 4252
master_index 4810 

4810 	 new pmg 	 3.0 = -log[Mg+2] _ mol/L;IS=0.25;Mg2+_free=0.001;K+_tot=0.22795;(Cl)1=0.1609;(HPO4)1=0.01905;(H2PO4)1=0.03095 _ Mg2+ (0.001 mol/L) _ 

du_index 4253
1443___previously matched datum___4253
3315___previously matched datum___4253
3315___previously matched datum___4253

1417___Keq___0.032979139___0.027
1417___reaction___ATP(aq) + carbamate(aq) = ADP(aq) + carbamoyl phosphate(aq)___ATP(aq) + ammonium carbamate(aq) = ADP(aq) + carbamoyl phosphate(aq)

matched pair: 
du_index 4294
master_index 1417 

1417 	 new pmg 	 mol/L;carbamate=0.000499;ATP=0.0000295;ADP=0.0000192;carbamoyl phosphate=0.0000205;(NH4)1(Cl)1=0.2;(Mg)1(Cl)2=0.01  

du_index 4295
1417___reaction___ATP(aq) + carbamate(aq) = ADP(aq) + carbamoyl phosphate(aq)___ATP(aq) + ammonium carbamate(aq) = ADP(aq) + carbamoyl phosphate(aq)
--> Failed index to match:  4295 ___ carbamate kinase

du_index 4296
1417___previously matched datum___4295
--> Failed index to match:  4296 ___ carbamate kinase

du_index 4297
1417___previously matched datum___4296
--> Failed index to match:  4297 ___ carbamate kinase

Completely unique standard_ids:  True
Unmatched standard_ids:  564


# Programmatically adding the manual curation

The unmatched entitites datums in the '2021-08-12_unmatched_TECR_datums.json' file from the previous code was manually curated. The manual curation was guided by the near misses of matches that were identified in the aforementioned JSON file. Slight heterogeneities in reaction strings, which were difficult to programmatically catch and correct, were a common source of missing a match. The manual curation was recorded and briefly explained in the 'Manual curation of the programmatically unmatched datums.txt' file, which utilizes comma delimiters for programmability and tabs for readability.

In [13]:
import re

# import the files
manual_curation = pandas.read_csv('Manual curation of the programmatically unmatched datums, comma delimited.txt', header = 0)
master_file = pandas.read_csv('2021-08-16_master_TECR_2.csv')
master_file = master_file.fillna('')
for column in master_file:
    if re.search('Unnamed', column):
        del master_file[column]

# remove tabs from the dataframe
headings = []
for column in manual_curation:
    headings.append(column.strip('\t'))
    for index, row in manual_curation[column].iteritems():
        manual_curation[column].iloc[index] = row.strip('\t')
        
manual_curation.columns = headings
display(manual_curation)

# parse the manually curated content
parsing_errors = []
for index, row in manual_curation.iterrows():
    
    # characterize the curated datums            
    master_file_ids = [row['Master file index']]
    add = False
    if re.search('New', master_file_ids[0]):
        add = True
        
    merge = False
    if not re.search('--', master_file_ids[0]) and not add:            
        merge = True
        # parse the corresponding master_file indices
        if re.search('-', master_file_ids[0]):
            master_file_ids = master_file_ids[0].split('-')
            lower = int(master_file_ids[0])
            upper = int(master_file_ids[1])

            if lower < upper:
                id_range = upper - lower
                master_file_ids = [id + lower for id in range(id_range + 1)]                
            
        elif re.search(r'\\', master_file_ids[0]):
            master_file_ids = master_file_ids[0].split('\\')   
        else:
            master_file_ids = [int(master_file_ids[0])]
                
    # parse the previously unmatched standard IDs
    standard_ids = [row['standard ID']]
    if re.search('-', standard_ids[0]):
        standard_ids = standard_ids[0].split('-')
        lower = int(standard_ids[0])
        upper = int(standard_ids[1])

        if lower < upper:
            id_range = upper - lower
            standard_ids = [id + lower for id in range(id_range + 1)]
       
    else:
        standard_ids = [int(standard_ids[0])]
            
    # add new datums to the master file
    print(standard_ids)
    print(master_file_ids)
    if add or merge:
        for standard_id_index in range(len(standard_ids)):
            standard_id = standard_ids[standard_id_index]
            print(standard_id)
            elad_row = equilibrator_2008.iloc[int(standard_id)]
            elad_index = elad_row['standard_id']
                        
            if add:
                # define the datum values to add
                add_id = elad_row['standard_id']
                add_enzyme = elad_row['enzyme_name']
                add_reference = elad_row['reference']
                add_method = elad_row['method']
                add_ec = elad_row['EC']
                add_kegg_reaction = elad_row['reaction']
                add_reaction = elad_row['description']
                add_pmg = elad_row['p_mg']
                add_k = elad_row['K_prime']
                if add_k is nan:
                    add_k = elad_row['K']
                add_temperature = elad_row['temperature']
                add_ionic_strength = elad_row['ionic_strength']
                add_ph = elad_row['p_h']
                
                # elad a new row at the end of master dataframe, according to master column organization
                master_file.loc[len(master_file.index)] = [add_id, add_enzyme, add_kegg_reaction, add_reaction, '', add_reference, add_temperature, add_ph, add_k, '', add_method, '', add_pmg, add_ec, '', '', '', add_ionic_strength, '']

            if merge:
                # match the standard id with the master_index
                match_index = standard_ids.index(standard_id)
                master_index = master_file_ids[match_index]
                master_row = master_file.iloc[int(master_index)]

                # merge the content of the equilibrator_2008 and master_file for the corresponding standard id
                redefine_master(master_row, elad_row, master_id = None, elad_id = elad_index)
                
    else:
        # characterize the curated datums            
        error = row['Error resolution']
        if re.search('Duplicate', error):
            print('The {} standard ID is a duplicate.'.format(standard_ids))
        elif re.search('already', error):
            print('The {} standard ID is already matched.'.format(standard_ids))
        else:
            parsing_errors.append(standard_ids)
            print('ERROR: The {} standard ID was not captured by the parsing.'.format(standard_ids))

if parsing_errors == []:
    parsing_errors = None
print('Parsing errors: ', parsing_errors)
            
# export the expanded master_file
display(master_file.tail(5))
csv_name = '2021-08-16_master_TECR_3.csv'
master_file.to_csv(csv_name)

standard ID           Error resolution Master file index
0           38            Duplicate of 37                --
1           77           Duplicate of 269                --
2        79-80       Chemical name change           708-709
3          114           Duplicate of 113                --
4          270  Proton omission\inclusion              1762
..         ...                        ...               ...
71        4170       already matched 4868                --
72        4191          Duplicate of 4191                --
73        4367          Duplicate of 4366                --
74        4467                        New               New
75        4493          Duplicate of 4492                --

[76 rows x 3 columns]

[38]
['--']
The [38] standard ID is a duplicate.
[77]
['--']
The [77] standard ID is a duplicate.
[79, 80]
[708, 709]
79

matched pair: 
elad_index 79
master_index 708 

80

matched pair: 
elad_index 80
master_index 709 

[114]
['--']
The [114] standard ID is a duplicate.
[270]
[1762]
270

matched pair: 
elad_index 270
master_index 1762 

[271]
[1763]
271

matched pair: 
elad_index 271
master_index 1763 

[283]
[2009]
283

matched pair: 
elad_index 283
master_index 2009 

[315]
['--']
The [315] standard ID is a duplicate.
[358]
[' \t\t--']
The [358] standard ID is a duplicate.
[449]
[' \t\t--']
The [449] standard ID is a duplicate.
[470]
['--']
The [470] standard ID is a duplicate.
[518]
[1835]
518

matched pair: 
elad_index 518
master_index 1835 

[674]
['--']
The [674] standard ID is a duplicate.
[729]
[2281]
729

matched pair: 
elad_index 729
master_index 2281 

[849, 850]
[3577, 3578]
849

matched pair: 
elad_index 849
master_index 3577 

3577 	 new EC 	 3.2.1.21 & 3.2.1.20
850

ma

standard_id               Enzyme:  \
5151        3975  alkaline phosphatase   
5152        3976  alkaline phosphatase   
5153        3977  alkaline phosphatase   
5154        3978  alkaline phosphatase   
5155        4467   aconitate hydratase   

                                 KEGG Reaction:  \
5151  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5152  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5153  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5154  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5155    kegg:C00311 = kegg:C00417 + kegg:C00001   

                                              Reaction: Reference:  \
5151  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5152  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5153  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5154  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5155        isocitrate(aq) = cis-aconitate(aq) + H2O(l)              

     Reference ID:   T [K]  pH      Keq Km                           Method:  \
5151     89ROM/DEM  308.15  7.0  490.00     chromatography and radioactivity   
5152     89ROM/DEM  308.15  7.8  184.00     chromatography and radioactivity   
5153     89ROM/DEM  308.15  7.8  100.00     chromatography and radioactivity   
5154     89ROM/DEM  308.15  7.8  100.00     chromatography and radioactivity   
5155     43KRE/EGG  311.15  7.4    0.69                          polarimetry   

     Buffer: Experimental conditions EC Value: solutes [mol / kg]  \
5151                            2.38   3.1.3.1                      
5152                            2.00   3.1.3.1                      
5153                            1.30   3.1.3.1                      
5154                            1.30   3.1.3.1                      
5155                                   4.2.1.3                      

     solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
5151                                                    
5152                                                    
5153                                                    
5154                                                    
5155                                                    

     Ionic strength [mol / kg] Enthalpy [kJ / mol]  
5151                                                
5152                                                
5153                                                
5154                                                
5155

# master_file containing glycolysis 

In [61]:
import pandas

glycolysis = pandas.read_csv('../../Publication/Curation_paper/EC values of glycolysis enzymes.csv')
master_file = pandas.read_csv('2021-09-02_master_TECR_2.csv')
# print(glycolysis, '\n')
# print(glycolysis.columns)
for index, row in glycolysis.iterrows():
#     master_data = master_file.loc[master_file['EC Value:'] == row['EC']]
    mask = master_file['EC Value:'].str.contains(row['EC'])
    if row['Enzyme'] == 'triose phosphate isomerase':
        questionable_mask = mask
    print(row['Enzyme'], '\t', row['EC'])
    print(mask.value_counts()[True])
    
# for index, entry in questionable_mask.iteritems():
#     if entry is True:
#         print(index, entry)

hexokinase 	 5.4.2.2
13
GPI 	 5.3.1.9
63
PFK 	 2.7.1.11
20
aldolase 	 4.1.2.13
113
triose phosphate isomerase 	 5.3.1.1
115
glyceraldehyde 3-phosphate dehydrogenase 	 1.2.1.12
98
phosphoglycerate kinase 	 2.7.2.3
79
phosphoglycerate mutase 	 5.4.2.1
72
enolase 	 4.2.1.11
94
pyruvate kinase 	 2.7.1.40
38


# Brainstorming

In [70]:
from to_precision import sci_notation, auto_notation

print(sci_notation(1234.0000, 2))
print(auto_notation(123, 2))

1.2e3
120


In [23]:
num = '298.15'
for ch in num:
    print(ord(ch))
float('298.15')

50
57
56
46
49
53


298.15

In [24]:
from string import printable

number = '298.l5'
for ch in number:
    print(ord(ch))
#.encode('utf-8').decode('utf-8', 'strict')
# number = ''.join(filter(lambda x: x in printable, number))
float(number)

50
57
56
46
108
53


ValueError: could not convert string to float: '298.l5'

In [14]:
import pandas
import re

du_et_al = pandas.read_excel('mmc2.xlsx', sheet_name = 'Table S1. TECRDB Keqs')
print(du_et_al.columns)
# second_time = False
for column in du_et_al:
#     if re.search('Reaction', column):
#         if second_time:
#             du_et_al.rename(columns = {column: 'reaction_string'}, inplace = True)
#         second_time = True
    if column == 'Reaction.1':
        du_et_al.rename(columns = {column: 'reaction_string'}, inplace = True)
print(du_et_al.columns)

Index(['Reaction', 'EC value', 'Method', 'Evaluation', 'Reaction.1',
       'Reaction formula in CID format', 'order', 'order id',
       'Reaction formula in python dictionary', 'T(K)', 'pH', 'Ionic strength',
       'pMg', 'K'', 'electrolytes', 'Buffer/reagents/solute added',
       'Reference_id', 'media conditions', 'exclude'],
      dtype='object')
Index(['Reaction', 'EC value', 'Method', 'Evaluation', 'reaction_string',
       'Reaction formula in CID format', 'order', 'order id',
       'Reaction formula in python dictionary', 'T(K)', 'pH', 'Ionic strength',
       'pMg', 'K'', 'electrolytes', 'Buffer/reagents/solute added',
       'Reference_id', 'media conditions', 'exclude'],
      dtype='object')
